In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import datetime
import numpy as np
import random
import itertools
from IPython.display import clear_output

In [3]:
def handle_table_to_line(mã):
    global df1
    df1= pd.read_excel("./All_prices/%s.xlsx"%(mã))
    # df1.rename(columns={'STT','Ngày','Giá Tham Chiếu','+/- (*)','% (*)','Đóng Cửa (*)','Khối Lượng','Mở Cửa (*)','Cao Nhất (*)','Thấp Nhất (*)','Giao Dịch Thỏa Thuận','Nước Ngoài Mua','Nước Ngoài Bán','Giá Trị(triệu đồng)'})
    df1.columns = [''] * len(df1.columns)
    header = df1.iloc[0].values
    df1.columns = header
    df1.drop(0,inplace=True)
    df1.drop(0,axis=1,inplace=True)
    df = df1[["Đóng Cửa (*)","Ngày"]]
    df.reset_index(inplace=True)
    df["Đóng Cửa (*)"]= df["Đóng Cửa (*)"].astype(float)
    df["Ngày"] = pd.to_datetime(df["Ngày"])
    df.sort_values(by="Ngày",ascending=True,inplace=True)
    
#     MA250= df["Đóng Cửa (*)"].rolling(250).mean()
    
#     fig, ax = plt.subplots()     
#     fig.set_size_inches(11.7, 8.27)
#     sns.lineplot(x='Ngày',y='Đóng Cửa (*)', data = df,ax = ax,sort=False)
    
#     plt.savefig('./%s_data/price/linechart/%s.png'%(ngành,mã))
    return df

In [4]:
def max_len(list_stock):
    global max_len
    i=0
    max_len=list_stock[0]
    for dataC in list_stock:
        clear_output()
        i+=1
        print(i)
        A= pd.read_excel("./All_prices/%s.xlsx"%(dataC))
        if len(A)>len(pd.read_excel("./All_prices/%s.xlsx"%(max_len))):
            max_len=dataC
        else:
            pass
    
    print("Tìm xong max_len",max_len)
    return max_len

In [5]:
def corr(ngành,list_stock,column_to_run):

    global cor_tab
    
    df_head= pd.read_excel("./All_prices/%s.xlsx"%(max_len),thousands=",", decimal=".")    
    print(1)
    
    header = df_head.iloc[0].values
    df_head.columns = header
    df_head.drop(0,inplace=True)
    df_head.drop(0,axis=1,inplace=True)
    df_head["Ngày"] = pd.to_datetime(df_head["Ngày"],dayfirst=True)
    df_head[column_to_run]= df_head[column_to_run].astype(float)
    df_head.sort_values(by="Ngày",ascending=True,inplace=True)
    
    cor_tab= pd.DataFrame((df_head[(df_head["Ngày"]>pd.to_datetime('31-12-2016',dayfirst=True))&(df_head["Ngày"]<= pd.to_datetime('31-12-2019',dayfirst=True))])[["Ngày",column_to_run]])
    
#     cor_tab.rename(columns={df_head.columns[6]:"A"})
    
    cor_tab.rename(columns={column_to_run:max_len},inplace=True)
    
    cor_tab.reset_index(drop=True,inplace=True)
    cor_tab.reset_index(inplace=True)
#     print(cor_tab)

    list_stock.remove(max_len)
    
    for mã in list_stock:
        df2= pd.read_excel("./All_prices/%s.xlsx"%(mã),thousands=",", decimal=".")
        
        print(list_stock.index(mã)+1,mã)
        
        header2 = df2.iloc[0].values
        df2.columns = header2
        df2.drop(0,inplace=True)
        df2.drop(0,axis=1,inplace=True)
        try:
            df2["Ngày"] = pd.to_datetime(df2["Ngày"],dayfirst=True)
            df2[column_to_run]= df2[column_to_run].astype(float)
            df2.sort_values(by="Ngày",ascending=True,inplace=True)
            df3 = df2[(df2['Ngày'] > pd.to_datetime('31-12-2016',dayfirst=True)) & (df2['Ngày'] <= pd.to_datetime('31-12-2019',dayfirst=True))][[column_to_run,"Ngày"]]
    #         print(df3)
            df3.drop(columns='Ngày',inplace=True)
        except:
            df2.drop(1,axis=0,inplace=True)
            df2["Ngày"] = pd.to_datetime(df2["Ngày"],dayfirst=True)
            df2[column_to_run]= df2[column_to_run].astype(float)
            df2.sort_values(by="Ngày",ascending=True,inplace=True)
            df3 = df2[(df2['Ngày'] > pd.to_datetime('31-12-2016',dayfirst=True)) & (df2['Ngày'] <= pd.to_datetime('31-12-2019',dayfirst=True))][[column_to_run,"Ngày"]]
    #         print(df3)
            df3.drop(columns='Ngày',inplace=True)
            
        if (len(df3)) >= (len(cor_tab)):
            K= df3.reset_index(drop=True)
            M= K.reset_index()
            M.columns=["index",mã]
            cor_tab=cor_tab.merge(M,how='inner',left_on= "index", right_on="index")
            
        else:
            appending=[]
            print(len(cor_tab)-len(df3))
            for i in range(len(cor_tab)-len(df3)):
                appending.append(np.nan)
            C=pd.DataFrame(appending)[0]
            D= C.append(df3)
            D=pd.DataFrame(D)
            D.reset_index(drop=True,inplace=True)
            D.reset_index(inplace=True)
#             print(D)
            D.drop(columns=0,inplace=True)
            D.columns=["index",mã]
        
            cor_tab=cor_tab.merge(D,how='inner',left_on= "index", right_on="index")
            
        clear_output()
        
#     cor_tab.drop(columns='Đóng Cửa (*)',inplace=True)
    cor_tab.drop(columns='index',inplace=True)
    cor_tab.reset_index(drop=True,inplace=True)
    
    cor_tab.dropna(axis=1, how='all',inplace=True)
#     cor_tab.drop(columns='Đóng Cửa (*)',inplace=True)
#   cor_tab.drop(0,inplace=True)
    return cor_tab

In [6]:
def indata(data):
    
    global col, prop
    
    col=list(data.columns.values)
    
    try:
        col.remove("Ngày")
    except:
        pass
    
    len_data=len(col)

    prop_rub=[]

    prop=[]

    for i in range(len_data):
        prop_rub.append(random.randint(0,10000))

    # Tính tổng của dãy chỉ số:
    sum_ind=sum(prop_rub)
    
    for things in prop_rub:
        prop.append(things/sum_ind)
    
    return col, prop

In [7]:
def PnL(list_pro,list_data,init_mon,datatab,name_pig):
    global total_pnl, unna_tab, day

    day= datatab["Ngày"]
    
    unna_tab1=datatab.fillna(method="bfill")
    unna_tab=unna_tab1.fillna(method="ffill")
    
    list_money=[]
    for pro in list_pro:
        list_money.append(pro*init_mon)
#     print(list_data)
    
    list_num=[]
    for money, data in zip(list_money, list_data):
        list_num.append(money/unna_tab[data][0])
        
    print(list_num)
    
    data_dict={}
    
    
    for smt, num in zip(list_data,list_num):
#         print(smt,num)
        data_list=[]
        for i in range(len(unna_tab)):
            A= num*unna_tab[smt][i]
        
            
            data_list.append(A)
        
        data_dict.update({smt : data_list})
    
    df_pnl= pd.DataFrame(data=data_dict)
    
    len_df = len(df_pnl)
#     print(df_pnl)
    total_pnl= df_pnl.sum(axis = 1, skipna = True) - init_mon
    total_pnl=pd.DataFrame(total_pnl)
    
    total_money = df_pnl.sum(axis = 1, skipna = True)
    total_money=pd.DataFrame(total_money)
    
    percentage_pnl= ((df_pnl.sum(axis = 1, skipna = True)/init_mon)-1)
    percentage_pnl= pd.DataFrame(percentage_pnl)
    
#     print(datatab["Ngày"])
    total_pnl["Ngày"]=day
    total_pnl.columns=["PNL","Ngày"]
    
    percentage_pnl["Ngày"]=day
    percentage_pnl.columns=["PNL","Ngày"]
    
    total_money["Ngày"]=day
    total_money.columns=["PNL","Ngày"]
    
    
#     holding_return = 100*((total_pnl[len(total_pnl)-1] - tot_int_val)/tot_int_val)
    
    
    return total_money

In [8]:
def random_walk(init_data,len_port):
    
    output=[]
    
    for i in range(0,len_port):
        output.append(init_data[random.randrange(0,len(init_data))])
    
    output.append("Ngày")
    
    return output
    

In [9]:
def sharpe(df):
    
    len_tab=len(df)

    ret_lis= list(df["PNL"])
    
    ret_lis=[]
    for i in range(0,len_tab-1):
        ret= ((df["PNL"].values[i+1]/df["PNL"].values[i])-1)
        ret_lis.append(ret)
    
    fir_tra_day=df["PNL"].values[0]
    las_tra_day=df["PNL"].values[len_tab-1]
    
    holding_ret= (las_tra_day-fir_tra_day)/1000000
    
    ret_arr=np.array(ret_lis)    

    std_ret=ret_arr.std()
    mean_ret=np.mean(ret_arr)
    
    cal_an_lis=[]
    for ret in ret_lis:
        cal_an_lis.append(ret+1)
    
    ite = np.array(cal_an_lis)
    geo_mean = (ite.prod()**(1.0/len(ite)) - 1)

    sharpe= holding_ret/len(df)
    
    day_lis=list(day)
    
    day_lis.pop(0)
    
    ret_df= pd.DataFrame({"Ngày":day_lis,"PNL":ret_lis})
    
    
        
    return sharpe

In [10]:
def sharpe2(df):
    global ret_df
    
    len_tab=len(df)

    ret_lis= list(df["PNL"])
    
    ret_lis=[]
    for i in range(0,len_tab-1):
        ret= ((df["PNL"].values[i+1]/df["PNL"].values[i])-1)
        ret_lis.append(ret)
    
    fir_tra_day=df["PNL"].values[0]
    las_tra_day=df["PNL"].values[len_tab-1]
    
    holding_ret= (las_tra_day-fir_tra_day)/fir_tra_day
    
    ret_arr=np.array(ret_lis)    

    std_ret=ret_arr.std()
    mean_ret=np.mean(ret_arr)
    
    cal_an_lis=[]
    for ret in ret_lis:
        cal_an_lis.append(ret+1)
    
    ite = np.array(cal_an_lis)
    geo_mean = (ite.prod()**(1.0/len(ite)) - 1)

    sharpe= geo_mean/std_ret
    
    day_lis=list(day)
    
    day_lis.pop(0)
    
    ret_df= pd.DataFrame({"Ngày":day_lis,"PNL":ret_lis})
    
    return sharpe

In [11]:
def get_top_liquid(data_liquid_tab,top):
    data_vol2=data_liquid_tab.drop(columns='Ngày')
    data_vol2=data_vol2.drop(columns='KSC')
    data_vol2=data_vol2.drop(columns='D26')
    unna_vol=data_vol2.apply(lambda x: x.fillna(x.mean()),axis=0)
    unna_vol_pos=unna_vol.mean()
    unna_vol_pos.sort_values(ascending=False, inplace=True)
    most_liquid=unna_vol_pos.keys()[0:top].values
    return most_liquid

In [12]:
def cal_daily_pnl(prop_tab,price_tab,innit_mon,looper):
    
    trial=(prop_tab.loc[[looper]]*innit_mon)
    trial2=1/(price_tab.loc[[looper]])

    num=pd.concat([trial, trial2], ignore_index=True).prod()

    resl = np.sum((price_tab.loc[looper+1]*num-price_tab.loc[looper]*num))
    
    return resl  

In [13]:
data= input("Nhập tên ngành:")
f= open("./%s/sorted_all_prices.txt" %(data), "r")
String_tên_mã= f.read()
list_stocks= String_tên_mã.split(",")
f.close()
try:
    list_stocks.remove("")
except:
    pass
print(len(list_stocks),list_stocks)

Nhập tên ngành:All_prices
1549 ['AAM', 'A32', 'AAA', 'AAV', 'ABC', 'ABI', 'ABT', 'AC4', 'ACB', 'ACC', 'ACE', 'ACL', 'ACM', 'ACS', 'ACV', 'ADC', 'ADP', 'ADS', 'AFX', 'AG1', 'AGC', 'AGD', 'AGF', 'AGM', 'AGP', 'AGR', 'AGX', 'ALP', 'ALT', 'ALV', 'AMC', 'AMD', 'AME', 'AMP', 'AMS', 'AMV', 'ANT', 'ANV', 'APC', 'APF', 'APG', 'API', 'APP', 'APS', 'APT', 'ARM', 'ART', 'ASA', 'ASD', 'ASIAGF', 'ASM', 'ASP', 'AST', 'ATA', 'ATB', 'ATD', 'ATG', 'ATS', 'AUM', 'AVC', 'AVF', 'AVS', 'B82', 'BAB', 'BAM', 'BAS', 'BAX', 'BBC', 'BBM', 'BBS', 'BBT', 'BCC', 'BCE', 'BCG', 'BCI', 'BCM', 'BCP', 'BDB', 'BDC', 'BDF', 'BDP', 'BDT', 'BDW', 'BED', 'BFC', 'BGM', 'BGW', 'BHC', 'BHK', 'BHN', 'BHP', 'BHS', 'BHT', 'BHV', 'BIC', 'BID', 'BII', 'BKC', 'BKH', 'BLF', 'BLI', 'BLN', 'BLT', 'BM9', 'BMC', 'BMD', 'BMF', 'BMI', 'BMJ', 'BMP', 'BMS', 'BNW', 'BOT', 'BPC', 'BPW', 'BQB', 'BRC', 'BRR', 'BRS', 'BSA', 'BSC', 'BSD', 'BSG', 'BSH', 'BSI', 'BSL', 'BSP', 'BSQ', 'BSR', 'BST', 'BT1', 'BT6', 'BTB', 'BTC', 'BTD', 'BTG', 'BTH', 'BTN',

In [11]:
# max_len_stock= max_len(list_stocks)
# print(max_len_stock)

In [14]:
max_len="REE"

In [18]:
# df=pd.read_excel("./All_prices/AAM.xlsx")

# header = df.iloc[0].values
# df.columns = header
# df.drop(0,inplace=True)
# df.drop(0,axis=1,inplace=True)

# df.columns

Index(['STT', 'Ngày', 'Giá Tham Chiếu', '+/- (*)', ' % (*)', 'Đóng Cửa (*)',
       'Khối Lượng', 'Mở Cửa  (*)', 'Cao Nhất (*)', 'Thấp Nhất (*)',
       'Giao Dịch Thỏa Thuận', 'Nước Ngoài Mua', 'Nước Ngoài Bán',
       'Giá Trị(triệu đồng)'],
      dtype='object')

In [22]:
# list_to_run=list_stocks.copy()
# volume=corr(data,list_to_run,"Cao Nhất (*)")
# print(volume)
# volume.to_excel('./Summary/High.xlsx',  engine='xlsxwriter' )

          Ngày    REE    AAM   A32    AAA  AAV    ABC    ABI    ABT  AC4  ...  \
0   2017-01-03  21.47   6.72   NaN  16.84  NaN  21.66  20.72  34.24  NaN  ...   
1   2017-01-04  21.69   7.07   NaN  17.21  NaN  21.66  19.85  34.24  NaN  ...   
2   2017-01-05  21.82   7.25   NaN  17.22  NaN  21.66  19.77  34.24  NaN  ...   
3   2017-01-06  21.77   7.07   NaN  16.98  NaN  21.66  19.41  34.24  NaN  ...   
4   2017-01-09  21.60   7.28   NaN  17.76  NaN  21.66  20.62  34.24  NaN  ...   
..         ...    ...    ...   ...    ...  ...    ...    ...    ...  ...  ...   
743 2019-12-25  36.25  12.50  28.0  12.95  8.3  10.70  30.20  33.90  4.5  ...   
744 2019-12-26  35.90  12.40  28.0  13.10  8.4   9.90  30.40  33.90  4.5  ...   
745 2019-12-27  35.90  12.80  28.0  12.95  8.4   9.80  30.30  35.50  4.5  ...   
746 2019-12-30  36.65  13.20  28.0  13.00  8.7   9.90  30.30  35.50  4.5  ...   
747 2019-12-31  36.65  12.80  28.0  12.90  8.8   9.90  30.30  36.00  4.5  ...   

     X77  XDH    XHC   XMC 

In [23]:
# list_to_run=list_stocks.copy()
# volume=corr(data,list_to_run,"Giao Dịch Thỏa Thuận")
# print(volume)
# volume.to_excel('./Summary/Agreement.xlsx',  engine='xlsxwriter' )

          Ngày        REE  AAM  A32  AAA  AAV  ABC        ABI  ABT  AC4  ...  \
0   2017-01-03        0.0  0.0  NaN  0.0  NaN  0.0        0.0  0.0  NaN  ...   
1   2017-01-04        0.0  0.0  NaN  0.0  NaN  0.0  1000000.0  0.0  NaN  ...   
2   2017-01-05        0.0  0.0  NaN  0.0  NaN  0.0        0.0  0.0  NaN  ...   
3   2017-01-06  2084450.0  0.0  NaN  0.0  NaN  0.0        0.0  0.0  NaN  ...   
4   2017-01-09        0.0  0.0  NaN  0.0  NaN  0.0        0.0  0.0  NaN  ...   
..         ...        ...  ...  ...  ...  ...  ...        ...  ...  ...  ...   
743 2019-12-25   300000.0  0.0  0.0  0.0  0.0  0.0        0.0  0.0  0.0  ...   
744 2019-12-26   350000.0  0.0  0.0  0.0  0.0  0.0        0.0  0.0  0.0  ...   
745 2019-12-27   320000.0  0.0  0.0  0.0  0.0  0.0        0.0  0.0  0.0  ...   
746 2019-12-30        0.0  0.0  0.0  0.0  0.0  0.0        0.0  0.0  0.0  ...   
747 2019-12-31        0.0  0.0  0.0  0.0  0.0  0.0        0.0  0.0  0.0  ...   

     X77  XDH  XHC  XMC  XMD  XPH  YBC 

In [24]:
# list_to_run=list_stocks.copy()
# volume=corr(data,list_to_run,"Nước Ngoài Mua")
# print(volume)
# volume.to_excel('./Summary/Foreign_buy.xlsx',  engine='xlsxwriter' )

          Ngày        REE  AAM  A32       AAA  AAV  ABC     ABI     ABT  AC4  \
0   2017-01-03    40000.0  0.0  NaN     800.0  NaN  0.0  1100.0   190.0  NaN   
1   2017-01-04    10250.0  0.0  NaN    1000.0  NaN  0.0   500.0   100.0  NaN   
2   2017-01-05        0.0  0.0  NaN       0.0  NaN  0.0   600.0  1190.0  NaN   
3   2017-01-06  2085250.0  0.0  NaN    1500.0  NaN  0.0   800.0     0.0  NaN   
4   2017-01-09        0.0  0.0  NaN     900.0  NaN  0.0   300.0    30.0  NaN   
..         ...        ...  ...  ...       ...  ...  ...     ...     ...  ...   
743 2019-12-25        0.0  0.0  0.0  134480.0  0.0  0.0   400.0     0.0  0.0   
744 2019-12-26        0.0  0.0  0.0    7490.0  0.0  0.0   100.0     0.0  0.0   
745 2019-12-27      670.0  0.0  0.0    8070.0  0.0  0.0   100.0     0.0  0.0   
746 2019-12-30     4550.0  0.0  0.0   10900.0  0.0  0.0     0.0     0.0  0.0   
747 2019-12-31        0.0  0.0  0.0    7000.0  0.0  0.0     0.0     0.0  0.0   

     ...  X77  XDH  XHC  XMC  XMD  XPH 

In [25]:
# list_to_run=list_stocks.copy()
# volume=corr(data,list_to_run,"Nước Ngoài Bán")
# print(volume)
# volume.to_excel('./Summary/Foreign_sell.xlsx',  engine='xlsxwriter' )

          Ngày        REE  AAM  A32      AAA  AAV  ABC  ABI  ABT  AC4  ...  \
0   2017-01-03      790.0  0.0  NaN      0.0  NaN  0.0  0.0  0.0  NaN  ...   
1   2017-01-04        0.0  0.0  NaN      0.0  NaN  0.0  0.0  0.0  NaN  ...   
2   2017-01-05    10000.0  0.0  NaN    500.0  NaN  0.0  0.0  0.0  NaN  ...   
3   2017-01-06  2086450.0  0.0  NaN      0.0  NaN  0.0  0.0  0.0  NaN  ...   
4   2017-01-09        0.0  0.0  NaN      0.0  NaN  0.0  0.0  0.0  NaN  ...   
..         ...        ...  ...  ...      ...  ...  ...  ...  ...  ...  ...   
743 2019-12-25     8240.0  0.0  0.0  10000.0  0.0  0.0  0.0  0.0  0.0  ...   
744 2019-12-26        0.0  0.0  0.0   9400.0  0.0  0.0  0.0  0.0  0.0  ...   
745 2019-12-27        0.0  0.0  0.0  15000.0  0.0  0.0  0.0  0.0  0.0  ...   
746 2019-12-30      670.0  0.0  0.0  17000.0  0.0  0.0  0.0  0.0  0.0  ...   
747 2019-12-31        0.0  0.0  0.0  51070.0  0.0  0.0  0.0  0.0  0.0  ...   

     X77  XDH  XHC  XMC  XMD  XPH  YBC  YBM     YEG  YTC  
0   

In [14]:
data1=pd.read_excel("./Summary/Close.xlsx")
data1.drop(columns='Unnamed: 0',inplace=True)

In [15]:
# data1

In [16]:
# run_data = list_stocks[0:3]
# run_data.append("Ngày")

counter=0
count_error=0

for i in range(1,10000):
    
    counter = i
    run_data = random_walk(list_stocks,5)
    
    try:
        print(i)
        indata(data1[run_data])
        A=PnL(prop,col,10000000,data1[run_data],i)
        B= sharpe(A)
        C= sharpe2(A)
        
        if B>=0.01 and C>=0.065:
            fig, ax = plt.subplots()     
            fig.set_size_inches(11.7, 8.27)
            sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
            plt.savefig("./Strategy/Passed/IMG/%d.png"%i)
            
            m=open("./Strategy/Passed/Text/%d.txt"%i,"w")
            for pro, stock in zip(prop,col):
                m.write(str(pro)+" "+stock + "\n")
            m.write("Straight-Sharpe:" + str(B)+ "\n")
            m.write("Sharpe:" + str(C))
            m.close()
            
        else: 
            fig, ax = plt.subplots()     
            fig.set_size_inches(11.7, 8.27)
            sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
            plt.savefig("./Strategy/Failed/IMG/%d.png"%i)
            
            m=open("./Strategy/Failed/Text/%d.txt"%i,"w")
            for pro, stock in zip(prop,col):
                m.write(str(pro)+ " " + stock + "\n")
            m.write("Straight-Sharpe:" + str(B)+ "\n")
            m.write("Sharpe:" + str(C))
            m.close()
        
        count_error -= 1
        
        clear_output()
    except:
        mk=open("./Strategy/Failed/Text/%d_error.txt"%i,"w")
        for stock in run_data:
            mk.write(stock+"\n")
        mk.close()
        clear_output()
        
        count_error += 1
    
    if count_error >= 300:
        break
        print("Stop by error!")
    else:
        pass

Error in callback <function install_repl_displayhook.<locals>.post_execute at 0x0CA1F150> (for post_execute):


MemoryError: In RendererAgg: Out of memory

RuntimeError: libpng signaled error

<Figure size 842.4x595.44 with 1 Axes>

RuntimeError: libpng signaled error

...

<Figure size 842.4x595.44 with 1 Axes>

MemoryError: In RendererAgg: Out of memory

<Figure size 842.4x595.44 with 1 Axes>

MemoryError: In RendererAgg: Out of memory

<Figure size 842.4x595.44 with 1 Axes>

In [17]:
# run_data = list_stocks[0:3]
# run_data.append("Ngày")

for i in range(counter,10000):
    
    counter = i
    run_data = random_walk(list_stocks,5)
    
    try:
        print(i)
        indata(data1[run_data])
        A=PnL(prop,col,10000000,data1[run_data],i)
        B= sharpe(A)
        C= sharpe2(A)
        
        if B>=0.01 and C>=0.065:
            fig, ax = plt.subplots()     
            fig.set_size_inches(11.7, 8.27)
            sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
            plt.savefig("./Strategy/Passed/IMG/%d.png"%i)
            
            m=open("./Strategy/Passed/Text/%d.txt"%i,"w")
            for pro, stock in zip(prop,col):
                m.write(str(pro)+" "+stock + "\n")
            m.write("Straight-Sharpe:" + str(B)+ "\n")
            m.write("Sharpe:" + str(C))
            m.close()
            
        else: 
            fig, ax = plt.subplots()     
            fig.set_size_inches(11.7, 8.27)
            sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
            plt.savefig("./Strategy/Failed/IMG/%d.png"%i)
            
            m=open("./Strategy/Failed/Text/%d.txt"%i,"w")
            for pro, stock in zip(prop,col):
                m.write(str(pro)+ " " + stock + "\n")
            m.write("Straight-Sharpe:" + str(B)+ "\n")
            m.write("Sharpe:" + str(C))
            m.close()
        
        count_error -= 1
        
        clear_output()
    except:
        mk=open("./Strategy/Failed/Text/%d_error.txt"%i,"w")
        for stock in run_data:
            mk.write(stock+"\n")
        mk.close()
        clear_output()
        
        count_error += 1
    
    if count_error >= 300:
        break
        print("Stop by error!")
    else:
        pass

In [15]:
i=1
run_data = random_walk(list_stocks,5)

try:
    print(i)
    indata(data1[run_data])
    A=PnL(prop,col,10000000,data1[run_data],i)
except:
    pass

1
[52377.2092600602, 209718.81122547534, 23818.47994527559, 638354.6271512276, 285145.83735754294]


In [16]:
A

PNL       Ngày
0    1.000000e+07 2017-01-03
1    9.981752e+06 2017-01-04
2    9.853681e+06 2017-01-05
3    9.808867e+06 2017-01-06
4    9.840570e+06 2017-01-09
..            ...        ...
743  2.041570e+07 2019-12-25
744  1.954332e+07 2019-12-26
745  1.913738e+07 2019-12-27
746  1.812240e+07 2019-12-30
747  1.708839e+07 2019-12-31

[748 rows x 2 columns]

In [18]:
# i=1
# prop = [0.0920, 0.1815, 0.6705, 0.0560]
# col= ["FPT","GVR","MBB","VPB"]

# A=PnL(prop,col,37689500,data1[["Ngày","FPT","GVR","MBB","VPB"]],i)
# B= sharpe(A)
# C= sharpe2(A)

# if B>=0.01 and C>=0.065:
#     fig, ax = plt.subplots()     
#     fig.set_size_inches(11.7, 8.27)
#     sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
#     plt.savefig("./Strategy/Passed/IMG/%d.png"%i)

#     m=open("./Strategy/Passed/Text/%d.txt"%i,"w")
#     for pro, stock in zip(prop,col):
#         m.write(str(pro)+" "+stock + "\n")
#     m.write("Straight-Sharpe:" + str(B)+ "\n")
#     m.write("Sharpe:" + str(C))
#     m.close()

# else: 
#     fig, ax = plt.subplots()     
#     fig.set_size_inches(11.7, 8.27)
#     sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
#     plt.savefig("./Strategy/Failed/IMG/%d.png"%i)

#     m=open("./Strategy/Failed/Text/%d.txt"%i,"w")
#     for pro, stock in zip(prop,col):
#         m.write(str(pro)+ " " + stock + "\n")
#     m.write("Straight-Sharpe:" + str(B)+ "\n")
#     m.write("Sharpe:" + str(C))
#     m.close()

In [19]:
# i=2
# prop = [0.6, 0.4]
# col= ["HDC","MBB"]

# A=PnL(prop,col,10000000,data1[["Ngày","HDC","MBB"]],i)
# B= sharpe(A)
# C= sharpe2(A)

# if B>=0.01 and C>=0.065:
#     fig, ax = plt.subplots()     
#     fig.set_size_inches(11.7, 8.27)
#     sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
#     plt.savefig("./Strategy/Passed/IMG/%d.png"%i)

#     m=open("./Strategy/Passed/Text/%d.txt"%i,"w")
#     for pro, stock in zip(prop,col):
#         m.write(str(pro)+" "+stock + "\n")
#     m.write("Straight-Sharpe:" + str(B)+ "\n")
#     m.write("Sharpe:" + str(C))
#     m.close()

# else: 
#     fig, ax = plt.subplots()     
#     fig.set_size_inches(11.7, 8.27)
#     sns.lineplot(x='Ngày',y='PNL', data = total_pnl,ax = ax,sort=False)
#     plt.savefig("./Strategy/Failed/IMG/%d.png"%i)

#     m=open("./Strategy/Failed/Text/%d.txt"%i,"w")
#     for pro, stock in zip(prop,col):
#         m.write(str(pro)+ " " + stock + "\n")
#     m.write("Straight-Sharpe:" + str(B)+ "\n")
#     m.write("Sharpe:" + str(C))
#     m.close()

In [20]:
# run_data=["Ngày","ABI","VCB","ACB"]

# indata(data1[run_data])

# A=PnL(prop,col,10000000,data1[run_data],1)
# # B= sharpe2(A)

# print(col)